In [1]:
!pip install --quiet -U altair
!pip install --quiet -U xgboost

import numpy as np
import pandas as pd
import altair as alt
import matplotlib as mpl
import matplotlib.pyplot as plt
import seaborn as sns
import math
import joblib
import collections

from sklearn.linear_model import LinearRegression
from sklearn.svm import SVR
from sklearn.ensemble import GradientBoostingRegressor, RandomForestRegressor
from sklearn.preprocessing import StandardScaler, PolynomialFeatures
from sklearn.model_selection import train_test_split, TimeSeriesSplit, GridSearchCV
from sklearn import pipeline
import sklearn
import xgboost
from xgboost import XGBRegressor

pd.options.display.max_columns = None
pd.options.display.max_rows = None
pd.options.mode.chained_assignment = None

alt.data_transformers.enable('default', max_rows=None)

%matplotlib inline
mpl.rcParams['figure.figsize'] = (12, 10)
mpl.rcParams.update({'font.size':22})
colors = plt.rcParams['axes.prop_cycle'].by_key()['color']

import warnings
warnings.filterwarnings("ignore")

# ML model functions

In [2]:
def LinearRegressionModel(df_train, verbose=0):
    model_LR = []
    
    if verbose>0:
        print('////////////////////////////////////////////// Linear regressor ////////////////////////////////')

    for p in range(1,7):
        tmp = df_train[df_train.P==p]
        X = tmp.iloc[:, :-1]
        Y = tmp.iloc[:,-1:].values.ravel()

        estimator = pipeline.Pipeline([
            ('poly', PolynomialFeatures(include_bias=False)),
            ('linear', LinearRegression())
        ])

        param_grid = {
            "poly__degree": [1,2],
            "linear__fit_intercept": [True, False],
            "linear__copy_X": [True, False],
            "linear__positive": [True, False]
        }

        grid_search = GridSearchCV(
            estimator=estimator,
            param_grid=param_grid,
            cv=TimeSeriesSplit(n_splits=10),
            scoring="neg_mean_squared_error",
            verbose=0,
            refit=True, 
            n_jobs=-1
        )

        grid_search.fit(X, Y)

        if verbose>0:
            print(grid_search.best_params_)
            print('Train RMS={:.3f}'.format(grid_search.best_score_))

        bestModel = grid_search.best_estimator_

        if verbose>0:
            print(bestModel)
        
        model_LR.append(bestModel)
        
        if verbose>0:
            print('{} done.'.format(p))

    return model_LR

def GradientBoostedModel(df_train, verbose=0):
    model_GB = []
    
    if verbose>0:
        print('////////////////////////////////////////////// Gradient boosted regressor ////////////////////////////////')

    for p in range(1,7):
        tmp = df_train.loc[df_train.P==p]
        X = tmp.iloc[:, :-1]
        Y = tmp.iloc[:,-1:].values.ravel()

        estimator = pipeline.Pipeline([
            ('gbc', GradientBoostingRegressor())
        ])

        param_grid = {
            "gbc__n_estimators": [10, 20, 50, 100, 150, 200, 250, 300],
            "gbc__learning_rate": [0.001, 0.01, 0.1, 1.0]
        }

        grid_search = GridSearchCV(
            estimator=estimator,
            param_grid=param_grid,
            cv=TimeSeriesSplit(n_splits=10),
            scoring="neg_mean_squared_error",
            verbose=0,
            refit=True, 
            n_jobs=-1
        )

        grid_search.fit(X, Y)

        if verbose>0:
            print(grid_search.best_params_)
            print('Train MSE={:.3f}'.format(grid_search.best_score_))

        bestModel = grid_search.best_estimator_

        if verbose>0:
            print(bestModel)

        model_GB.append(bestModel)
        
        if verbose>0:
            print('{} done.'.format(p))

    return model_GB

def RandomForestModel(df_train, verbose=0):
    model_RF = []
    
    if verbose>0:
        print('////////////////////////////////////////////// Random Forest regressor ////////////////////////////////')

    for p in range(1,7):
        tmp = df_train.loc[df_train.P==p]
        X = tmp.iloc[:, :-1]
        Y = tmp.iloc[:,-1:].values.ravel()

        estimator = pipeline.Pipeline([
            ('rf', RandomForestRegressor(bootstrap=True))
        ])

        param_grid = {
            "rf__n_estimators": [2, 4, 5, 10, 20, 50, 100, 150, 200],
            "rf__max_depth":[2,4,5,10,20,50]
        }

        grid_search = GridSearchCV(
            estimator=estimator,
            param_grid=param_grid,
            cv=TimeSeriesSplit(n_splits=10),
            scoring="neg_mean_squared_error",
            verbose=0,
            refit=True, 
            n_jobs=-1
        )

        grid_search.fit(X, Y)

        if verbose>0:
            print(grid_search.best_params_)
            print('Train MSE={:.3f}'.format(grid_search.best_score_))

        bestModel = grid_search.best_estimator_

        if verbose>0:
            print(bestModel)

        model_RF.append(bestModel)
        
        if verbose>0:
            print('{} done.'.format(p))

    return model_RF

def XGBoostModel(df_train, verbose=0):
    model_XGB = []
    
    if verbose>0:
        print('////////////////////////////////////////////// XGBoost regressor ////////////////////////////////')

    for p in range(1,7):
        tmp = df_train.loc[df_train.P==p]
        X = tmp.iloc[:, :-1]
        Y = tmp.iloc[:,-1:].values.ravel()

        estimator = pipeline.Pipeline([
            ('xgb', XGBRegressor(colsample_bytree=0.8))
        ])


        param_grid = {
            "xgb__n_estimators": [10, 20, 50, 100, 150, 200, 250, 300],
            "xgb__max_depth":[2,4,5,10,20,50],
            "xgb__eta":[0.001,0.01,0.1],
            "xgb__subsample":[0.5,0.7,0.8]
        }


        grid_search = GridSearchCV(
            estimator=estimator,
            param_grid=param_grid,
            cv=TimeSeriesSplit(n_splits=10),
            scoring="neg_mean_squared_error",
            verbose=0,
            refit=True, 
            n_jobs=-1
        )

        grid_search.fit(X, Y)

        if verbose>0:
            print(grid_search.best_params_)
            print('Train MSE={:.3f}'.format(grid_search.best_score_))

        bestModel = grid_search.best_estimator_

        if verbose>0:
            print(bestModel)

        model_XGB.append(bestModel)
        
        if verbose>0:
            print('{} done.'.format(p))

    return model_XGB

def SupportVectorModel(df_train, verbose=0):
    model_SV = []
    
    if verbose>0:
        print('////////////////////////////////////////////// Support vector regressor ////////////////////////////////')

    for p in range(1,7):
        tmp = df_train.loc[df_train.P==p]
        X = tmp.iloc[:, :-1]
        Y = tmp.iloc[:,-1:].values.ravel()

        estimator = pipeline.Pipeline([
            ('svr', SVR(cache_size=1000))
        ])


        param_grid = {
            "svr__C": [0.01, 0.1, 1.0, 10.0],
            "svr__kernel": ['poly','rbf'],
            "svr__degree":[1,2]
        }


        grid_search = GridSearchCV(
            estimator=estimator,
            param_grid=param_grid,
            cv=TimeSeriesSplit(n_splits=10),
            scoring="neg_mean_squared_error",
            verbose=0,
            refit=True, 
            n_jobs=-1
        )

        grid_search.fit(X, Y)

        if verbose>0:
            print(grid_search.best_params_)
            print('Train MSE={:.3f}'.format(grid_search.best_score_))

        bestModel = grid_search.best_estimator_

        if verbose>0:
            print(bestModel)

        model_SV.append(bestModel)
        
        if verbose>0:
            print('{} done.'.format(p))

    return model_SV
print('Done')

Done


# Create training data (6 obs as history and 7th is the target)

In [3]:
df_data = pd.read_csv('../Data/Fitted_all_exp.csv')
df_data.rename(columns={'expM':'M'}, inplace=True)
df_data.head()

P    W  Exp         M
0  1  0.0    1  1.000000
1  1  0.1    1  0.994767
2  1  0.2    1  0.988913
3  1  0.3    1  0.983263
4  1  0.4    1  0.975513

In [4]:
tmp_df = []
hl = 6
for p in range(1,7):
    wl = df_data.W[df_data.P==p].nunique()
    for exp in range(1,352):
        tmp = df_data[np.logical_and(df_data.P==p, df_data.Exp==exp)]
        tmp.sort_values(['W'], ascending=True, inplace=True)
        tmp.reset_index(drop=True, inplace=True)

        for i in range(0, wl-hl):
            t = [p,exp]
            
            for j in range(hl+1):
                t.extend([tmp.W[i+j],tmp.M[i+j]])
            
            tmp_df.append(t)
        
    print('{} done.'.format(p))

    
cols = ['P','Exp']
for i in range(1, hl+1):
    cols.extend([f"w{i}", f"m{i}"])
cols.extend([f"w{hl+1}", 'target'])

print(cols)

df_train = pd.DataFrame(tmp_df,columns=cols)
del [tmp_df]

df_train.P = df_train.P.astype(int)
df_train.Exp = df_train.Exp.astype(int)
df_train.to_csv('../Data/Synthetic_train_data.csv', index=False)
df_train.head()

1 done.
2 done.
3 done.
4 done.
5 done.
6 done.
['P', 'Exp', 'w1', 'm1', 'w2', 'm2', 'w3', 'm3', 'w4', 'm4', 'w5', 'm5', 'w6', 'm6', 'w7', 'target']


P  Exp   w1        m1   w2        m2   w3        m3   w4        m4   w5  \
0  1    1  0.0  1.000000  0.1  0.994767  0.2  0.988913  0.3  0.983263  0.4   
1  1    1  0.1  0.994767  0.2  0.988913  0.3  0.983263  0.4  0.975513  0.5   
2  1    1  0.2  0.988913  0.3  0.983263  0.4  0.975513  0.5  0.969977  0.6   
3  1    1  0.3  0.983263  0.4  0.975513  0.5  0.969977  0.6  0.960551  0.7   
4  1    1  0.4  0.975513  0.5  0.969977  0.6  0.960551  0.7  0.953878  0.8   

         m5   w6        m6   w7    target  
0  0.975513  0.5  0.969977  0.6  0.960551  
1  0.969977  0.6  0.960551  0.7  0.953878  
2  0.960551  0.7  0.953878  0.8  0.944605  
3  0.953878  0.8  0.944605  0.9  0.936483  
4  0.944605  0.9  0.936483  1.0  0.928113

# Train models and save the best model

In [7]:
df_train = pd.read_csv('../Data/Synthetic_train_data.csv')
print(df_train.shape)
df_train.head()

(621270, 16)


P  Exp   w1        m1   w2        m2   w3        m3   w4        m4   w5  \
0  1    1  0.0  1.000000  0.1  0.994767  0.2  0.988913  0.3  0.983263  0.4   
1  1    1  0.1  0.994767  0.2  0.988913  0.3  0.983263  0.4  0.975513  0.5   
2  1    1  0.2  0.988913  0.3  0.983263  0.4  0.975513  0.5  0.969977  0.6   
3  1    1  0.3  0.983263  0.4  0.975513  0.5  0.969977  0.6  0.960551  0.7   
4  1    1  0.4  0.975513  0.5  0.969977  0.6  0.960551  0.7  0.953878  0.8   

         m5   w6        m6   w7    target  
0  0.975513  0.5  0.969977  0.6  0.960551  
1  0.969977  0.6  0.960551  0.7  0.953878  
2  0.960551  0.7  0.953878  0.8  0.944605  
3  0.953878  0.8  0.944605  0.9  0.936483  
4  0.944605  0.9  0.936483  1.0  0.928113

In [8]:
model_GBR = GradientBoostedModel(df_train)
joblib.dump(model_GBR, '../Model/GB.sav')
print('Gradient boosted regression done')

Gradient boosted regression done


In [9]:
model_RF = RandomForestModel(df_train)
joblib.dump(model_RF, '../Model/RF.sav')
print('Random forest regression done')

Random forest regression done


In [10]:
model_XGB = XGBoostModel(df_train)
joblib.dump(model_XGB, '../Model/XGB.sav')
print('XGBoost regression done')

XGBoost regression done


# Test on real data

In [11]:
df_real = pd.read_csv('../Data/All_p_w_m.csv')
df_real = df_real[df_real.W<15]
df_real.W = np.round(df_real.W, decimals=1)
df_real.sort_values(['P','Exp','W'], ascending=True, inplace=True)
df_real = df_real[['P','Exp','W','M']]
df_real.head()

P  Exp    W         M
0     1    1  0.0  1.000000
351   1    1  0.2  0.995567
702   1    1  0.4  0.981047
1053  1    1  0.6  0.976002
1404  1    1  0.8  0.969323

In [12]:
df_data = pd.read_csv('../Data/Fitted_all_exp.csv')
df_newData = None
for p in range(1,7):
    ws = df_real.W[df_real.P==p].unique()
    #print(ws)
    df_pre = df_data[np.logical_and(df_data.P==p, df_data.W.isin(ws))]
    #print(df_pre.W.unique())
    df_post = df_data[np.logical_and(df_data.P==p, df_data.W>max(ws))]
    tmp = pd.concat([df_pre, df_post], ignore_index=True)
    del [df_pre, df_post]

    if df_newData is None:
        df_newData = pd.DataFrame(tmp)
    else:
        df_newData = pd.concat([df_newData, tmp], ignore_index=True)
    del [tmp]
    
print(df_newData.W.unique())
df_newData.sample(10)

[ 0.   0.2  0.4  0.6  0.8  1.   1.2  1.3  1.4  1.5  1.6  1.7  1.8  1.9
  2.   2.1  2.2  2.3  2.4  2.5  2.6  2.7  2.8  2.9  3.   3.1  3.2  3.3
  3.4  3.5  3.6  3.7  3.8  3.9  4.   4.1  4.2  4.3  4.4  4.5  4.6  4.7
  4.8  4.9  5.   5.1  5.2  5.3  5.4  5.5  5.6  5.7  5.8  5.9  6.   6.1
  6.2  6.3  6.4  6.5  6.6  6.7  6.8  6.9  7.   7.1  7.2  7.3  7.4  7.5
  7.6  7.7  7.8  7.9  8.   8.1  8.2  8.3  8.4  8.5  8.6  8.7  8.8  8.9
  9.   9.1  9.2  9.3  9.4  9.5  9.6  9.7  9.8  9.9 10.  10.1 10.2 10.3
 10.4 10.5 10.6 10.7 10.8 10.9 11.  11.1 11.2 11.3 11.4 11.5 11.6 11.7
 11.8 11.9 12.  12.1 12.2 12.3 12.4 12.5 12.6 12.7 12.8 12.9 13.  13.1
 13.2 13.3 13.4 13.5 13.6 13.7 13.8 13.9 14.  14.1 14.2 14.3 14.4 14.5
 14.6 14.7 14.8 14.9 15.  15.1 15.2 15.3 15.4 15.5 15.6 15.7 15.8 15.9
 16.  16.1 16.2 16.3 16.4 16.5 16.6 16.7 16.8 16.9 17.  17.1 17.2 17.3
 17.4 17.5 17.6 17.7 17.8 17.9 18.  18.1 18.2 18.3 18.4 18.5 18.6 18.7
 18.8 18.9 19.  19.1 19.2 19.3 19.4 19.5 19.6 19.7 19.8 19.9 20.  20.1
 20.2 

P     W  Exp      expM
281667  3   4.8  289  0.510830
318916  4  19.4   72  0.169677
506335  6  27.0  119  0.126345
387083  4   5.1  342  0.499081
356479  4   6.0  221  0.434677
334737  4   7.6  135  0.360738
175103  2  12.6  251  0.275278
278813  3  10.9  278  0.293776
106575  2   4.6    3  0.556253
290393  3  29.4  321  0.163031

In [20]:
real_filled = []
hl = 6

df_data.sort_values(['P','Exp','W'], ascending=True, inplace=True)
df_real.sort_values(['P','Exp','W'], ascending=True, inplace=True)

for p in range(1,7):
    for exp in range(1, 352):
        gen = df_data.loc[np.logical_and(df_data.P==p, df_data.Exp==exp), ['W','expM']]
        real = df_real.loc[np.logical_and(df_real.P==p, df_real.Exp==exp), ['W','M']]
        
        i=0
        for w in gen.W.unique():
            i+=1
            if i==hl+1:
                break
                
            m = gen.expM[gen.W==w].values[0]
            if w in real.W:
                m = real.M[real.W==w].values[0]
                
            real_filled.append([p, exp, w, m])
            
df_real_filled = pd.DataFrame(real_filled, columns=['P','Exp','W','M'])
df_real_filled.sample(10)

P  Exp    W         M
482    1   81  0.2  0.991850
2471   2   61  0.5  0.983142
10762  6   39  0.4  0.989833
5215   3  168  0.1  1.000007
4785   3   96  0.3  0.998751
2405   2   50  0.5  0.982885
11506  6  163  0.4  0.991292
3271   2  195  0.1  0.999279
8874   5   76  0.0  1.000000
1824   1  305  0.0  1.000000

In [15]:
model_GB = joblib.load('../Model/GB.sav')
model_RF = joblib.load('../Model/RF.sav')
model_XGB = joblib.load('../Model/XGB.sav')

In [21]:
test = []
allWs = sorted(np.round(df_data.W.unique(), decimals=1))
hl = 6

for p in range(1,7):
    for exp in range(1, 352):
        #tmpLR = []
        tmpGB = []
        tmpRF = []
        tmpXGB = []
        
        #W = sorted(df_data.W[np.logical_and(df_data.P==p, df_data.Exp==exp)].unique())
        
        W = sorted(df_real_filled.W[np.logical_and(df_real_filled.P==p, df_real_filled.Exp==exp)].unique())
        print(W)
        break

[0.0, 0.1, 0.2, 0.3, 0.4, 0.5]
[0.0, 0.1, 0.2, 0.3, 0.4, 0.5]
[0.0, 0.1, 0.2, 0.3, 0.4, 0.5]
[0.0, 0.1, 0.2, 0.3, 0.4, 0.5]
[0.0, 0.1, 0.2, 0.3, 0.4, 0.5]
[0.0, 0.1, 0.2, 0.3, 0.4, 0.5]


In [22]:
test = []
allWs = sorted(np.round(df_data.W.unique(), decimals=1))
hl = 6

for p in range(1,7):
    for exp in range(1, 352):
        #tmpLR = []
        tmpGB = []
        tmpRF = []
        tmpXGB = []
        
        #W = sorted(df_data.W[np.logical_and(df_data.P==p, df_data.Exp==exp)].unique())
        
        W = sorted(df_real_filled.W[np.logical_and(df_real_filled.P==p, df_real_filled.Exp==exp)].unique())
        
        
        for w in W[:hl]:
            #m = df_data.M[np.logical_and(df_data.P==p, np.logical_and(df_data.Exp==exp, df_data.W==w))].values[0]
            
            m = df_real_filled.M[np.logical_and(df_real_filled.P==p, np.logical_and(df_real_filled.Exp==exp, df_real_filled.W==w))].values[0]

            test.append([p,exp,w,m,m,m])
            #tmpLR.append(w)
            #tmpLR.append(m)
            tmpGB.append(w)
            tmpGB.append(m)
            tmpRF.append(w)
            tmpRF.append(m)
            tmpXGB.append(w)
            tmpXGB.append(m)
            
        #print('real m=', df_real.M[np.logical_and(df_real.P==p, np.logical_and(df_real.Exp==exp, df_real.W==W[4]))].values[0])
        
        term = 1
        W_new = [x for x in allWs if x>W[hl-1]]
        #print(len(W_new))
        for w in W_new:
            #print(w)
            b = [p, exp, w]
            #tmpLR.append(w)
            tmpGB.append(w)
            tmpRF.append(w)
            tmpXGB.append(w)
            
            a = [p,exp]
            a.extend(tmpGB)
            a = np.array(a).reshape(1,-1)
            #print(a)
            m = model_GB[p-1].predict(a)[0]
            #print('m=',m)
            b.append(m)
            tmpGB.append(m)
            
            a = [p,exp]
            a.extend(tmpRF)
            a = np.array(a).reshape(1,-1)
            #print(a)
            m = model_RF[p-1].predict(a)[0]
            #print('m=',m)
            b.append(m)
            tmpRF.append(m)
            
            a = [p,exp]
            a.extend(tmpXGB)
            a = np.array(a).reshape(1,-1)
            #print(a)
            m = model_XGB[p-1].predict(a)[0]
            #print('m=',m)
            b.append(m)
            tmpXGB.append(m)
            
            #print(tmpLR)
            #print(tmpGB)
            #print(tmpRF)
            #print(tmpXGB)
            
            test.append(b)
            
            #tmpLR.pop(0)
            #tmpLR.pop(0)
            
            tmpGB.pop(0)
            tmpGB.pop(0)
            
            tmpRF.pop(0)
            tmpRF.pop(0)
            
            tmpXGB.pop(0)
            tmpXGB.pop(0)
            
            #term += 1
            
            #if term==3:
             #   break
                
            #print('\n\n')
        
    print(p, 'Done')
        
#test
df_test = pd.DataFrame(test, columns=['P','Exp','W','M_GB','M_RF','M_XGB'])
del [test]
df_test.to_csv('../Data/Real_data_projected.csv', index = False)
print('Saving done....', df_test.shape)
df_test.sample(10)

1 Done
2 Done
3 Done
4 Done
5 Done
6 Done
Saving done.... (633906, 6)


P  Exp     W      M_GB      M_RF     M_XGB
477474  5  183   8.8  0.391697  0.387127  0.387188
65456   1  218  13.9  0.347174  0.274384  0.273787
9464    1   32  13.3  0.281572  0.269968  0.267975
521479  5  329  14.7  0.391686  0.254705  0.253075
97651   1  325  12.7  0.466262  0.310132  0.312020
242866  3  105  26.0  0.183635  0.151190  0.146201
240029  3   96  13.2  0.348738  0.242389  0.242061
479278  5  189   8.6  0.391974  0.395094  0.395288
14852   1   50  10.3  0.356671  0.352472  0.350643
349768  4  110   0.6  0.995067  0.995277  0.995522

In [4]:
df_test = pd.read_csv('../Data/Real_data_projected.csv')
print(df_test.shape)
df_test.head()

(633906, 6)


P  Exp    W      M_GB      M_RF     M_XGB
0  1    1  0.0  1.000000  1.000000  1.000000
1  1    1  0.1  0.994767  0.994767  0.994767
2  1    1  0.2  0.988913  0.988913  0.988913
3  1    1  0.3  0.983263  0.983263  0.983263
4  1    1  0.4  0.975513  0.975513  0.975513

In [27]:
mn = {'M_GB':'Gradient boosted', 'M_RF':'Random forest', 'M_XGB':'Extreme gradient boosted'}
fig, axs = plt.subplots(nrows=3, ncols=1, sharex=False, figsize=(30,60), dpi=350)
i=0
for c in ['M_GB','M_RF','M_XGB']:
    tmp = df_test.groupby(['P','W'])[c].apply(lambda x: np.average(x)).reset_index()
    tmp.columns = ['P','W','M']
    #plt.figure(dpi=300, figsize=(25,15))
    for p in range(1, 7):
        t = tmp[tmp.P==p]
        axs[i].plot(t.W, t.M, '-', label='$p_z$={}'.format(p))
        
    axs[i].legend(loc='best')
    axs[i].set(xlabel='$\omega$')
    axs[i].set(ylabel='$\Delta\mathfrak{M}(\omega)$')
    axs[i].set_title('ML method={}'.format(mn[c]))
    i+=1

#plt.savefig("../newImg/Predicted_values.pdf".format(c), format="pdf", bbox_inches="tight")
plt.show()

In [5]:
mn = {'M_GB':'Gradient boosted', 'M_RF':'Random forest', 'M_XGB':'Extreme gradient boosted'}
fig, axs = plt.subplots(nrows=1, ncols=3, sharey=True, figsize=(60,20), dpi=350, layout='constrained')
i=0
for ct, c in enumerate(['M_GB','M_RF','M_XGB']):
    df_avg = df_test.groupby(['P','W'])[c].apply(lambda x: np.average(x)).reset_index()
    df_avg.columns = ['P','W','M']

    df_std = df_test.groupby(['P','W'])[c].apply(lambda x: np.std(x)).reset_index()
    df_std.columns = ['P','W','Err']

    df_g = df_avg.merge(df_std, on=['P','W'])
    del [df_avg,df_std]
    
    df_g.to_csv('../Data/Model_{}_avg_std_M.csv'.format(c), index=False)
    
    #plt.figure(dpi=300, figsize=(25,15))
    for p in range(1, 7):
        t = df_g[df_g.P==p]
        axs[i].errorbar(t.W, t.M,yerr=t.Err, fmt='-o', label='$p_z$={}'.format(p))
    
    axs[i].set_xlabel('$\omega$', fontsize=55)
    axs[i].set_xticklabels([str(int(x)) for x in axs[i].get_xticks()], fontsize=40)
    axs[i].set_title(f'{mn[c]}', y=0.95, pad=20.0, fontsize=48)
    
    if ct==0: 
        axs[i].legend(loc='best', prop={'size':48})
        axs[i].set_ylabel('$\mathfrak{M}(\omega)$', fontsize=55)
        axs[i].set_yticklabels([str(round(x,1)) for x in axs[i].get_yticks()], fontsize=40)
    
    i+=1
    
#plt.savefig("../newImg/With_error_bar.pdf".format(c), format="pdf", bbox_inches="tight")
plt.show()